In [1]:
# import libraries
import numpy as np
import pandas as pd
import pickle
from sqlalchemy import create_engine

import re
import nltk
nltk.download(['omw-1.4', 'punkt', 'stopwords', 'wordnet', 'averaged_perceptron_tagger'])
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer

from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.multioutput import MultiOutputClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.metrics import classification_report, roc_auc_score

from xgboost import XGBClassifier


[nltk_data] Downloading package omw-1.4 to
[nltk_data]     /Users/yilizhaomacpro/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yilizhaomacpro/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/yilizhaomacpro/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/yilizhaomacpro/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yilizhaomacpro/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/xgboost/compat.py:36: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with 

In [2]:
# load data from database
engine = create_engine('sqlite:///DisasterResponse.db')
df = pd.read_sql_table(table_name='message_table', con=engine)
X = df['message']
Y = df.iloc[:, 4:]

ValueError: Table message_table not found

In [3]:
# Some Y variables only have one category
Y.nunique()[Y.nunique() == 1].index

Index(['child_alone'], dtype='object')

### 2. Write a tokenization function to process your text data

In [4]:
def tokenize(text):
    
    # Normalization
    text = re.sub(r"[^a-zA-Z0-9]", " ", text.lower()) 
    
    # Tokenization
    words = word_tokenize(text)
    
    # Stop words removal
    words = [w for w in words if words not in stopwords.words("english")]
    
    # Stemming and Lemmatizing
    tokens = [PorterStemmer().stem(w) for w in words]
    lemmatizer = WordNetLemmatizer()
    
    clean_tokens = []
    for tok in tokens:
        clean_tok = lemmatizer.lemmatize(tok).lower().strip()
        clean_tokens.append(clean_tok)

    return clean_tokens

### 3. Build a machine learning pipeline
This machine pipeline should take in the `message` column as input and output classification results on the other 36 categories in the dataset. You may find the [MultiOutputClassifier](http://scikit-learn.org/stable/modules/generated/sklearn.multioutput.MultiOutputClassifier.html) helpful for predicting multiple target variables.

In [5]:
# Random forest pipeline
pipeline_rf = Pipeline([
        ('vect', CountVectorizer(tokenizer=tokenize)),
        ('tfidf', TfidfTransformer()),
        ('clf', MultiOutputClassifier(RandomForestClassifier(random_state = 42)))
])

### 4. Train pipeline
- Split data into train and test sets
- Train pipeline

In [6]:
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, test_size=0.2, random_state=42)
print(X_train.shape)
print(X_test.shape)
print(Y_train.shape)
print(Y_test.shape)
pipeline_rf.fit(X_train, Y_train)

(8030,)
(2008,)
(8030, 36)
(2008, 36)


Pipeline(steps=[('vect',
                 CountVectorizer(tokenizer=<function tokenize at 0x7fe369c68700>)),
                ('tfidf', TfidfTransformer()),
                ('clf',
                 MultiOutputClassifier(estimator=RandomForestClassifier(random_state=42)))])

### 5. Test your model
Report the f1 score, precision and recall for each output category of the dataset. You can do this by iterating through the columns and calling sklearn's `classification_report` on each.

In [7]:
Y_pred = pipeline_rf.predict(X_test)
Y_pred_proba = pipeline_rf.predict_proba(X_test)

In [8]:
print(classification_report(Y_test.values, Y_pred, target_names=Y_test.columns))

                        precision    recall  f1-score   support

               related       0.80      0.90      0.84      1307
               request       0.83      0.68      0.75       706
                 offer       0.00      0.00      0.00         3
           aid_related       0.81      0.68      0.74       785
          medical_help       0.50      0.02      0.03       114
      medical_products       1.00      0.10      0.18        59
     search_and_rescue       0.00      0.00      0.00        36
              security       0.00      0.00      0.00        25
              military       0.00      0.00      0.00        14
           child_alone       0.00      0.00      0.00         0
                 water       0.87      0.51      0.64       135
                  food       0.90      0.64      0.74       280
               shelter       0.94      0.34      0.50       197
              clothing       0.00      0.00      0.00        15
                 money       0.00      

/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [9]:
print(Y.columns[9])
Y.iloc[:, 9].unique()

child_alone


array([0.])

In [8]:
def displayAUC(Y_test, Y_pred_proba, category_names):
    # Save probability in a 2d numpy array (n_category * n_test)
    Y_pred_proba_array = np.array([1-x[0] for x in Y_pred_proba[0]])
    for i in range(1,len(Y_pred_proba)):
        prob = np.array([1-x[0] for x in Y_pred_proba[i]])
        Y_pred_proba_array = np.vstack((Y_pred_proba_array, prob))
    
    # AUC score
    avg_auc = 0
    num_auc = 0
    for i in range(len(Y_pred_proba)):
        try:
            auc = roc_auc_score(Y_test.values[:,i], Y_pred_proba_array[i,:])
            avg_auc += auc
            num_auc += 1
            print(str(i) + " "  + category_names[i] + " " + str(round(auc,4)))
        except ValueError:
            print(str(i) + " "  + category_names[i] + " NA")  
    avg_auc /= num_auc
    print("Average AUC is: ", avg_auc)

In [11]:
displayAUC(Y_test, Y_pred_proba, Y.columns)

0 related 0.8537
1 request 0.8995
2 offer 0.6365
3 aid_related 0.89
4 medical_help 0.817
5 medical_products 0.8207
6 search_and_rescue 0.7044
7 security 0.7162
8 military 0.6186
9 child_alone NA
10 water 0.9819
11 food 0.9693
12 shelter 0.9667
13 clothing 0.838
14 money 0.8377
15 missing_people 0.4959
16 refugees 0.7201
17 death 0.8684
18 other_aid 0.8093
19 infrastructure_related 0.7472
20 transport 0.5297
21 buildings 0.9453
22 electricity 0.8606
23 tools 0.7498
24 hospitals 0.8862
25 shops 0.7604
26 aid_centers 0.6008
27 other_infrastructure 0.7561
28 weather_related 0.9027
29 floods 0.7126
30 storm 0.9309
31 fire 0.5298
32 earthquake 0.9209
33 cold 0.5865
34 other_weather 0.6284
35 direct_report 0.8776
Average AUC is:  0.781981553914978


### 6. Improve your model
Use grid search to find better parameters. 

In [ ]:
pipeline_rf.get_params()

In [13]:
parameters_rf = {
    'clf__estimator__n_estimators': (100, 200, 300),
    'clf__estimator__max_depth':(None, 50, 100), 
    'clf__estimator__min_samples_leaf':(1, 3, 5),
    'clf__estimator__min_samples_split':(2, 3, 5)
} 

cv_rf = GridSearchCV(pipeline_rf, param_grid=parameters_rf, n_jobs=1, verbose=3, cv=5)
cv_rf.fit(X_train, Y_train)

Fitting 5 folds for each of 81 candidates, totalling 405 fits
[CV 1/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.334 total time=  43.1s
[CV 2/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.341 total time=  42.4s
[CV 3/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.342 total time=  43.0s
[CV 4/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.353 total time=  42.7s
[CV 5/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.342 total time=  42.9s
[CV 1/5] END clf__

[CV 1/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.285 total time=  29.2s
[CV 2/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.287 total time=  28.9s
[CV 3/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.293 total time=  29.3s
[CV 4/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.296 total time=  29.1s
[CV 5/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.303 total time=  29.4s
[CV 1/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=3,

[CV 1/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.255 total time=  27.0s
[CV 2/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.259 total time=  26.8s
[CV 3/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.273 total time=  26.6s
[CV 4/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.256 total time=  26.7s
[CV 5/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.277 total time=  26.5s
[CV 1/5] END clf__estimator__max_depth=None, clf__estimator__min_samples_leaf=5,

[CV 1/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.309 total time=  35.6s
[CV 2/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.300 total time=  34.8s
[CV 3/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.323 total time=  35.7s
[CV 4/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.321 total time=  35.7s
[CV 5/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.307 total time=  35.5s
[CV 1/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=1, clf__estima

[CV 2/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.271 total time=  26.8s
[CV 3/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.280 total time=  27.0s
[CV 4/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.265 total time=  26.8s
[CV 5/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.285 total time=  26.9s
[CV 1/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.268 total time=  41.5s
[CV 2/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=3, clf__estima

[CV 3/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.271 total time=  25.2s
[CV 4/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.257 total time=  25.2s
[CV 5/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.266 total time=  25.2s
[CV 1/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.253 total time=  38.2s
[CV 2/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.255 total time=  37.8s
[CV 3/5] END clf__estimator__max_depth=50, clf__estimator__min_samples_leaf=5, clf__estima

[CV 4/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.347 total time=  41.6s
[CV 5/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.341 total time=  41.7s
[CV 1/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.338 total time=18.7min
[CV 2/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.350 total time=33.7min
[CV 3/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=1, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.344 total time=17.3min
[CV 4/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=1, clf__

[CV 4/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.291 total time=  28.7s
[CV 5/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.302 total time=  28.9s
[CV 1/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.281 total time=  45.2s
[CV 2/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.290 total time=  44.7s
[CV 3/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=3, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.295 total time=  45.6s
[CV 4/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=3, clf__

[CV 4/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.256 total time=  26.4s
[CV 5/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=100;, score=0.276 total time=  26.6s
[CV 1/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.253 total time=  40.7s
[CV 2/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.263 total time=  40.0s
[CV 3/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=5, clf__estimator__min_samples_split=2, clf__estimator__n_estimators=200;, score=0.272 total time=  40.7s
[CV 4/5] END clf__estimator__max_depth=100, clf__estimator__min_samples_leaf=5, clf__

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('vect',
                                        CountVectorizer(tokenizer=<function tokenize at 0x7ff2310b09d0>)),
                                       ('tfidf', TfidfTransformer()),
                                       ('clf',
                                        MultiOutputClassifier(estimator=RandomForestClassifier(random_state=42)))]),
             n_jobs=1,
             param_grid={'clf__estimator__max_depth': (None, 50, 100),
                         'clf__estimator__min_samples_leaf': (1, 3, 5),
                         'clf__estimator__min_samples_split': (2, 3, 5),
                         'clf__estimator__n_estimators': (100, 200, 300)},
             verbose=3)

In [15]:
cv_rf.best_params_

{'clf__estimator__max_depth': None,
 'clf__estimator__min_samples_leaf': 1,
 'clf__estimator__min_samples_split': 2,
 'clf__estimator__n_estimators': 200}

### 7. Test your model
Show the accuracy, precision, and recall of the tuned model.  

Since this project focuses on code quality, process, and  pipelines, there is no minimum performance metric needed to pass. However, make sure to fine tune your models for accuracy, precision and recall to make your project stand out - especially for your portfolio!

In [16]:
Y_pred = cv_rf.predict(X_test)
Y_pred_proba = cv_rf.predict_proba(X_test)
print(classification_report(Y_test.values, Y_pred, target_names=Y_test.columns))

                        precision    recall  f1-score   support

               related       0.79      0.90      0.84      1307
               request       0.83      0.69      0.75       706
                 offer       0.00      0.00      0.00         3
           aid_related       0.81      0.69      0.74       785
          medical_help       0.60      0.03      0.05       114
      medical_products       1.00      0.12      0.21        59
     search_and_rescue       0.00      0.00      0.00        36
              security       0.00      0.00      0.00        25
              military       0.00      0.00      0.00        14
           child_alone       0.00      0.00      0.00         0
                 water       0.91      0.51      0.65       135
                  food       0.91      0.68      0.77       280
               shelter       0.95      0.37      0.53       197
              clothing       0.00      0.00      0.00        15
                 money       0.00      

/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [17]:
displayAUC(Y_test, Y_pred_proba, Y.columns)

0 related 0.8556
1 request 0.9008
2 offer 0.621
3 aid_related 0.8924
4 medical_help 0.8219
5 medical_products 0.8249
6 search_and_rescue 0.732
7 security 0.7521
8 military 0.6194
9 child_alone NA
10 water 0.9828
11 food 0.9713
12 shelter 0.9677
13 clothing 0.8517
14 money 0.8403
15 missing_people 0.5035
16 refugees 0.7403
17 death 0.8958
18 other_aid 0.8119
19 infrastructure_related 0.7383
20 transport 0.5675
21 buildings 0.9496
22 electricity 0.8224
23 tools 0.7405
24 hospitals 0.8535
25 shops 0.7379
26 aid_centers 0.7172
27 other_infrastructure 0.7585
28 weather_related 0.9049
29 floods 0.6994
30 storm 0.9414
31 fire 0.5857
32 earthquake 0.9271
33 cold 0.6158
34 other_weather 0.6173
35 direct_report 0.8809
Average AUC is:  0.7898105739302713


### 8. Try improving your model further. Here are a few ideas:
* try other machine learning algorithms
* add other features besides the TF-IDF

In [7]:
# XGboost pipeline
pipeline_xgb = Pipeline([
        ('vect', CountVectorizer(tokenizer=tokenize)),
        ('tfidf', TfidfTransformer()),
        ('clf', MultiOutputClassifier(XGBClassifier(random_state = 42)))
])

In [15]:
pipeline_xgb.fit(X_train, Y_train)

/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[20:38:11] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[20:38:12] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[20:38:13] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to '

[20:38:27] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[20:38:28] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[20:38:29] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to '

Pipeline(steps=[('vect',
                 CountVectorizer(tokenizer=<function tokenize at 0x7fbda9240940>)),
                ('tfidf', TfidfTransformer()),
                ('clf',
                 MultiOutputClassifier(estimator=XGBClassifier(base_score=None,
                                                               booster=None,
                                                               colsample_bylevel=None,
                                                               colsample_bynode=None,
                                                               colsample_bytree=None,
                                                               enable_categorical=False,
                                                               gamma=None,
                                                               gpu_id=None,
                                                               importance_type=None,
                                                               interaction_cons

In [16]:
Y_pred = pipeline_xgb.predict(X_test)
Y_pred_proba = pipeline_xgb.predict_proba(X_test)
print(classification_report(Y_test.values, Y_pred, target_names=Y_test.columns))

                        precision    recall  f1-score   support

               related       0.86      0.83      0.84      1307
               request       0.79      0.73      0.76       706
                 offer       0.00      0.00      0.00         3
           aid_related       0.80      0.72      0.76       785
          medical_help       0.59      0.19      0.29       114
      medical_products       0.65      0.25      0.37        59
     search_and_rescue       0.67      0.06      0.10        36
              security       0.00      0.00      0.00        25
              military       0.00      0.00      0.00        14
           child_alone       0.00      0.00      0.00         0
                 water       0.85      0.87      0.86       135
                  food       0.86      0.87      0.87       280
               shelter       0.81      0.70      0.75       197
              clothing       0.80      0.53      0.64        15
                 money       0.60      

/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [17]:
displayAUC(Y_test, Y_pred_proba, Y.columns)

0 related 0.8654
1 request 0.8959
2 offer 0.8613
3 aid_related 0.8933
4 medical_help 0.7828
5 medical_products 0.773
6 search_and_rescue 0.7198
7 security 0.5593
8 military 0.5894
9 child_alone NA
10 water 0.9753
11 food 0.9657
12 shelter 0.964
13 clothing 0.8573
14 money 0.8436
15 missing_people 0.6204
16 refugees 0.6808
17 death 0.8666
18 other_aid 0.8217
19 infrastructure_related 0.7045
20 transport 0.5844
21 buildings 0.9403
22 electricity 0.8252
23 tools 0.6517
24 hospitals 0.8258
25 shops 0.5814
26 aid_centers 0.6962
27 other_infrastructure 0.729
28 weather_related 0.8785
29 floods 0.6681
30 storm 0.8947
31 fire 0.4061
32 earthquake 0.9134
33 cold 0.7455
34 other_weather 0.6435
35 direct_report 0.877
Average AUC is:  0.7743093676357328


In [12]:
# Adaboost pipeline
pipeline_ada = Pipeline([
        ('vect', CountVectorizer(tokenizer=tokenize)),
        ('tfidf', TfidfTransformer()),
        ('clf', MultiOutputClassifier(AdaBoostClassifier(random_state = 42)))
])

In [22]:
pipeline_ada.fit(X_train, Y_train)

Pipeline(steps=[('vect',
                 CountVectorizer(tokenizer=<function tokenize at 0x7fbda9240940>)),
                ('tfidf', TfidfTransformer()),
                ('clf',
                 MultiOutputClassifier(estimator=AdaBoostClassifier(random_state=42)))])

In [23]:
Y_pred = pipeline_ada.predict(X_test)
Y_pred_proba = pipeline_ada.predict_proba(X_test)
print(classification_report(Y_test.values, Y_pred, target_names=Y_test.columns))

                        precision    recall  f1-score   support

               related       0.84      0.82      0.83      1307
               request       0.77      0.67      0.72       706
                 offer       0.00      0.00      0.00         3
           aid_related       0.82      0.69      0.75       785
          medical_help       0.48      0.25      0.33       114
      medical_products       0.63      0.29      0.40        59
     search_and_rescue       0.42      0.14      0.21        36
              security       0.00      0.00      0.00        25
              military       0.00      0.00      0.00        14
           child_alone       0.00      0.00      0.00         0
                 water       0.80      0.86      0.83       135
                  food       0.84      0.76      0.80       280
               shelter       0.82      0.69      0.75       197
              clothing       0.50      0.33      0.40        15
                 money       0.64      

/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [24]:
displayAUC(Y_test, Y_pred_proba, Y.columns)

0 related 0.8485
1 request 0.8876
2 offer 0.6703
3 aid_related 0.8802
4 medical_help 0.804
5 medical_products 0.7336
6 search_and_rescue 0.7427
7 security 0.7022
8 military 0.5669
9 child_alone NA
10 water 0.9798
11 food 0.9548
12 shelter 0.9515
13 clothing 0.7882
14 money 0.8603
15 missing_people 0.6257
16 refugees 0.6746
17 death 0.8381
18 other_aid 0.8026
19 infrastructure_related 0.7081
20 transport 0.5885
21 buildings 0.9321
22 electricity 0.8349
23 tools 0.3704
24 hospitals 0.7492
25 shops 0.595
26 aid_centers 0.5988
27 other_infrastructure 0.7323
28 weather_related 0.871
29 floods 0.7021
30 storm 0.9167
31 fire 0.4615
32 earthquake 0.925
33 cold 0.6027
34 other_weather 0.7223
35 direct_report 0.8695
Average AUC is:  0.7569165893774146


In [13]:
# Add more feature
class StartingVerbExtractor(BaseEstimator, TransformerMixin):

    def starting_verb(self, text):
        sentence_list = nltk.sent_tokenize(text)
        for sentence in sentence_list:
            pos_tags = nltk.pos_tag(tokenize(sentence))
            
            if len(pos_tags) > 1:
                first_word, first_tag = pos_tags[0]
                if first_tag in ['VB', 'VBP'] or first_word == 'RT':
                    return True
                
        return False

    def fit(self, X, y=None):
        return self

    def transform(self, X):
        X_tagged = pd.Series(X).apply(self.starting_verb)
        return pd.DataFrame(X_tagged)

In [9]:
pipeline2 = Pipeline([
    ('features', FeatureUnion([

        ('text_pipeline', Pipeline([
            ('vect', CountVectorizer(tokenizer=tokenize)),
            ('tfidf', TfidfTransformer())
        ])),

        ('starting_verb', StartingVerbExtractor())
    ])),

    #('clf', MultiOutputClassifier(AdaBoostClassifier(random_state = 42)))
    ('clf', MultiOutputClassifier(XGBClassifier(random_state = 42)))
    #('clf', MultiOutputClassifier(estimator=RandomForestClassifier(random_state=42, max_depth=None,min_samples_leaf=1,
                                                                   #min_samples_split=2, n_estimators=200)))
])


In [10]:
pipeline2.fit(X_train, Y_train)
Y_pred = pipeline2.predict(X_test)
Y_pred_proba = pipeline2.predict_proba(X_test)
print(classification_report(Y_test.values, Y_pred, target_names=Y_test.columns))
displayAUC(Y_test, Y_pred_proba, Y.columns)

/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[23:46:24] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[23:46:24] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[23:46:25] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to '

[23:46:37] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[23:46:38] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[23:46:39] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to '

/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [13]:
pipeline_xgb.get_params()

{'memory': None,
 'steps': [('vect',
   CountVectorizer(tokenizer=<function tokenize at 0x7fda18905940>)),
  ('tfidf', TfidfTransformer()),
  ('clf',
   MultiOutputClassifier(estimator=XGBClassifier(base_score=None, booster=None,
                                                 colsample_bylevel=None,
                                                 colsample_bynode=None,
                                                 colsample_bytree=None,
                                                 enable_categorical=False,
                                                 gamma=None, gpu_id=None,
                                                 importance_type=None,
                                                 interaction_constraints=None,
                                                 learning_rate=None,
                                                 max_delta_step=None,
                                                 max_depth=None,
                                                 m

In [9]:
parameters_xgb = {
    'clf__estimator__n_estimators': (100, 200),
    'clf__estimator__max_depth': (3, 6),
    'clf__estimator__learning_rate': (0.01, 0.1),
    'clf__estimator__colsample_bytree': (0.7, 1),
    'clf__estimator__min_child_weight': (1, 5, 10),
    'clf__estimator__subsample': (0.7, 1),
}
cv_xgb = GridSearchCV(pipeline_xgb, param_grid=parameters_xgb, n_jobs=1, verbose=3, cv=5)
cv_xgb.fit(X_train, Y_train)

Fitting 5 folds for each of 96 candidates, totalling 480 fits


/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[23:09:28] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[23:09:29] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[23:09:29] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to '

[23:09:36] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[23:09:37] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[23:09:37] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to '

/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


...

[05:24:56] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[05:24:57] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[05:24:57] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to '

/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[05:42:36] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[05:42:37] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[05:42:38] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to '

[05:42:56] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[05:42:57] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[05:42:57] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_44tbtwf8c1/croots/recipe/xgboost-split_1659548960882/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to '

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('vect',
                                        CountVectorizer(tokenizer=<function tokenize at 0x7fe369c68700>)),
                                       ('tfidf', TfidfTransformer()),
                                       ('clf',
                                        MultiOutputClassifier(estimator=XGBClassifier(base_score=None,
                                                                                      booster=None,
                                                                                      colsample_bylevel=None,
                                                                                      colsample_bynode=None,
                                                                                      colsample_bytree=None,
                                                                                      enable_categorical=False,
                                                                  

In [15]:
cv_xgb.best_estimator_

Pipeline(steps=[('vect',
                 CountVectorizer(tokenizer=<function tokenize at 0x7fe369c68700>)),
                ('tfidf', TfidfTransformer()),
                ('clf',
                 MultiOutputClassifier(estimator=XGBClassifier(base_score=None,
                                                               booster=None,
                                                               colsample_bylevel=None,
                                                               colsample_bynode=None,
                                                               colsample_bytree=0.7,
                                                               enable_categorical=False,
                                                               gamma=None,
                                                               gpu_id=None,
                                                               importance_type=None,
                                                               interaction_const

In [10]:
Y_pred = cv_xgb.predict(X_test)
Y_pred_proba = cv_xgb.predict_proba(X_test)
print(classification_report(Y_test.values, Y_pred, target_names=Y_test.columns))
displayAUC(Y_test, Y_pred_proba, Y.columns)

                        precision    recall  f1-score   support

               related       0.86      0.82      0.84      1307
               request       0.79      0.71      0.74       706
                 offer       0.00      0.00      0.00         3
           aid_related       0.83      0.71      0.76       785
          medical_help       0.60      0.18      0.28       114
      medical_products       0.80      0.27      0.41        59
     search_and_rescue       1.00      0.06      0.11        36
              security       0.00      0.00      0.00        25
              military       0.00      0.00      0.00        14
           child_alone       0.00      0.00      0.00         0
                 water       0.84      0.92      0.88       135
                  food       0.87      0.88      0.87       280
               shelter       0.81      0.68      0.74       197
              clothing       0.80      0.53      0.64        15
                 money       0.67      

/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [13]:
pipeline_ada.get_params()

{'memory': None,
 'steps': [('vect',
   CountVectorizer(tokenizer=<function tokenize at 0x7fe369c68700>)),
  ('tfidf', TfidfTransformer()),
  ('clf',
   MultiOutputClassifier(estimator=AdaBoostClassifier(random_state=42)))],
 'verbose': False,
 'vect': CountVectorizer(tokenizer=<function tokenize at 0x7fe369c68700>),
 'tfidf': TfidfTransformer(),
 'clf': MultiOutputClassifier(estimator=AdaBoostClassifier(random_state=42)),
 'vect__analyzer': 'word',
 'vect__binary': False,
 'vect__decode_error': 'strict',
 'vect__dtype': numpy.int64,
 'vect__encoding': 'utf-8',
 'vect__input': 'content',
 'vect__lowercase': True,
 'vect__max_df': 1.0,
 'vect__max_features': None,
 'vect__min_df': 1,
 'vect__ngram_range': (1, 1),
 'vect__preprocessor': None,
 'vect__stop_words': None,
 'vect__strip_accents': None,
 'vect__token_pattern': '(?u)\\b\\w\\w+\\b',
 'vect__tokenizer': <function __main__.tokenize(text)>,
 'vect__vocabulary': None,
 'tfidf__norm': 'l2',
 'tfidf__smooth_idf': True,
 'tfidf__subli

In [20]:
parameters_ada = {
        'tfidf__use_idf': (True, False),
        'clf__estimator__n_estimators': [50, 60, 70]
}

cv_ada = GridSearchCV(pipeline_ada, param_grid=parameters_ada, n_jobs=1, verbose=3, cv=5)
cv_ada.fit(X_train, Y_train)

Fitting 5 folds for each of 6 candidates, totalling 30 fits
[CV 1/5] END clf__estimator__n_estimators=50, tfidf__use_idf=True;, score=0.362 total time=  30.1s
[CV 2/5] END clf__estimator__n_estimators=50, tfidf__use_idf=True;, score=0.382 total time=  29.7s
[CV 3/5] END clf__estimator__n_estimators=50, tfidf__use_idf=True;, score=0.375 total time=  29.4s
[CV 4/5] END clf__estimator__n_estimators=50, tfidf__use_idf=True;, score=0.392 total time=  30.1s
[CV 5/5] END clf__estimator__n_estimators=50, tfidf__use_idf=True;, score=0.372 total time=  29.9s
[CV 1/5] END clf__estimator__n_estimators=50, tfidf__use_idf=False;, score=0.380 total time=  25.6s
[CV 2/5] END clf__estimator__n_estimators=50, tfidf__use_idf=False;, score=0.371 total time=  25.7s
[CV 3/5] END clf__estimator__n_estimators=50, tfidf__use_idf=False;, score=0.380 total time=  26.8s
[CV 4/5] END clf__estimator__n_estimators=50, tfidf__use_idf=False;, score=0.387 total time=  26.4s
[CV 5/5] END clf__estimator__n_estimators=50,

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('vect',
                                        CountVectorizer(tokenizer=<function tokenize at 0x7fe369c68700>)),
                                       ('tfidf', TfidfTransformer()),
                                       ('clf',
                                        MultiOutputClassifier(estimator=AdaBoostClassifier(random_state=42)))]),
             n_jobs=1,
             param_grid={'clf__estimator__n_estimators': [50, 60, 70],
                         'tfidf__use_idf': (True, False)},
             verbose=3)

In [24]:
cv_ada.best_estimator_

Pipeline(steps=[('vect',
                 CountVectorizer(tokenizer=<function tokenize at 0x7fe369c68700>)),
                ('tfidf', TfidfTransformer(use_idf=False)),
                ('clf',
                 MultiOutputClassifier(estimator=AdaBoostClassifier(random_state=42)))])

In [25]:
Y_pred = cv_ada.predict(X_test)
Y_pred_proba = cv_ada.predict_proba(X_test)
print(classification_report(Y_test.values, Y_pred, target_names=Y_test.columns))
displayAUC(Y_test, Y_pred_proba, Y.columns)

                        precision    recall  f1-score   support

               related       0.85      0.81      0.83      1307
               request       0.78      0.69      0.73       706
                 offer       0.00      0.00      0.00         3
           aid_related       0.81      0.70      0.75       785
          medical_help       0.50      0.24      0.32       114
      medical_products       0.61      0.32      0.42        59
     search_and_rescue       0.50      0.14      0.22        36
              security       0.50      0.04      0.07        25
              military       0.00      0.00      0.00        14
           child_alone       0.00      0.00      0.00         0
                 water       0.84      0.87      0.85       135
                  food       0.85      0.76      0.80       280
               shelter       0.82      0.65      0.73       197
              clothing       0.56      0.33      0.42        15
                 money       0.71      

/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/yilizhaomacpro/opt/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


### 9. Export your model as a pickle file

In [37]:
filename = 'model.pkl'
pickle.dump(pipeline2, open(filename, 'wb'))

### 10. Use this notebook to complete `train.py`
Use the template file attached in the Resources folder to write a script that runs the steps above to create a database and export a model based on a new dataset specified by the user.